In [1]:
import glob
import ujson

In [2]:
import unicodedata

def remove_accents(input_str):
    input_str = input_str.lower().replace("й", "-&-")
    nfkd_form = unicodedata.normalize('NFKD', input_str).replace("-&-", "й")
    return u"".join([c for c in nfkd_form if not unicodedata.combining(c)])


In [3]:
parsed_jsons = []

# for fname in glob.glob("extracted_json_big/*/*"):

for fname in glob.glob("extracted_json_good/*/*"):
    with open(fname, 'r') as f:
        for line in f:
            parsed = ujson.loads(line)
            parsed_jsons.append(parsed)


In [4]:
import pandas as pd

data_df = pd.DataFrame.from_records(parsed_jsons)

In [5]:
import sys
sys.path.append('../clustering_system/')

import re
import os
import pymorphy2
from collections import Counter

from preprocessing.aitexta.tokenization import RegexpTokenizer
from preprocessing.aitexta.tokenization import SpacyRulesRussianTokenizer
from preprocessing.aitexta.utils import FunctionalTransformer
from preprocessing.aitexta.lemmatization import Pymorphy2Lemmatizer
from preprocessing.aitexta.feature_filtering import StopTokensRemover
from preprocessing.aitexta.feature_filtering import RegexpFilter
from preprocessing.aitexta.feature_filtering import BASE_RU_NONTOKEN_REGEXPS
from preprocessing.aitexta.feature_extracting import TopMineNgrammer
from preprocessing.aitexta.ner_extracting import Pymorphy2NerExtractor
from preprocessing.aitexta.utils import MergerTransformer
from preprocessing.aitexta.pipeline import SequentialPipeline

In [6]:
this_file_path = os.path.dirname('../clustering_system/preprocessing/')
STOP_TOKENS_RELATIVE_PATH = 'aitexta/feature_filtering/stop_words_files/BASE_UNIVERSAL.txt'
STOP_TOKENS_FILE = os.path.join(this_file_path, STOP_TOKENS_RELATIVE_PATH)

In [7]:
# TODO
# specSymb = {"«", "»", "—", "“", "-", "№"}
# specSymb =  punctuation + "«»—“-№"
# pattern = re.compile("[" + re.escape(specSymb) + "]")


In [9]:
class MainModelPreprocessor:
    def __init__(self, n_jobs=1, verbose=False):
        html_tag_replacer = FunctionalTransformer(lambda x: re.sub('</?[^>]+>', ' <TAG> ', x))

        quot_replacer = FunctionalTransformer(lambda x: re.sub('&quot;', ' " ', x))

        url_replacer = FunctionalTransformer(lambda x: re.sub('(http|www)\S+', ' <URL> ', x))

        mail_regexp = "[\S]*@( )?[\S]+(\s?[\.,][a-zA-Z0-9]+)?"
        mail_replacer = FunctionalTransformer(lambda x: re.sub(mail_regexp, ' <MAIL> ', x))

        space_deleter = FunctionalTransformer(lambda x: " ".join(x.split()))

        nontoken_regexps = (
            u'[^a-zA-Zа-яА-ЯёЁ .?!]+',
        )

        token_regexps = (
            '<[a-zа-яёA-ZА-ЯЁ.?!]+>',
            'не_[a-zа-яёA-ZА-ЯЁ.!?]+',
        )

        token_main_filter = RegexpFilter(
            nontoken_regexps_list=nontoken_regexps,
            token_regexps_list=token_regexps,
            conflict_behaviour='keep',
            n_jobs=n_jobs,
        )

        def replace_person_with_tag(sentence, ner_tags):
            formated_sentence = [
                token if ner_tag not in {'PER'} else '<person>'
                for token, ner_tag in zip(sentence, ner_tags)
            ]

            return formated_sentence

        persons_replacer = MergerTransformer(
            merge_function=replace_person_with_tag,
            transformers=[
                FunctionalTransformer(lambda x: x),
                Pymorphy2NerExtractor(mode='tag', n_jobs=n_jobs),
            ]
        )

        replace_special_sequences = SequentialPipeline(steps=[
            ('html_tag_replacer', html_tag_replacer),
            ('quout_replacer', quot_replacer),
            ('url_replacer', url_replacer),
            ('mail_replacer', mail_replacer),
            ('delete_additional_spaces', space_deleter),
            ('clean_unicode', FunctionalTransformer(lambda x: remove_accents(x)))
        ], verbose=verbose)

        self.text_to_lemmatized = SequentialPipeline(steps=[
            ('replacer', replace_special_sequences),
            ('tokenization', SpacyRulesRussianTokenizer()),
            ('persons_replacer', persons_replacer),
            ('lemmatization', Pymorphy2Lemmatizer(n_jobs=n_jobs)),
        ], verbose=verbose)

        self.remove_stop_words_from_lemmatized = SequentialPipeline(steps=[
            ('stop_words_remover', StopTokensRemover(stop_tokens_file=STOP_TOKENS_FILE,
                                                     n_jobs=n_jobs)),
            ('stop_regexp_remover', token_main_filter)
        ], verbose=verbose)

        self.lemmatized_to_ngramms = SequentialPipeline(steps=[
            ('ngrammer', TopMineNgrammer(stop_tokens_file=STOP_TOKENS_FILE,
                                         nontoken_regexps=BASE_RU_NONTOKEN_REGEXPS,
                                         allow_delimiters_in_ngramm=True,
                                         output_type='string_ngramm',
                                         n_jobs=n_jobs))
        ], verbose=verbose)

    def fit_transform(self, X):
        X = self._clean_dataframe(X)

        X['raw_lemmatized'] = self.text_to_lemmatized.fit_transform(X['text'].values)

        X['lemmatized'] = self.remove_stop_words_from_lemmatized.fit_transform(
            X['raw_lemmatized'].values
        )
        X['ngramms'] = self.lemmatized_to_ngramms.fit_transform(X['raw_lemmatized'].values)

        for column in ['raw_lemmatized', 'lemmatized', 'ngramms']:
            X[column] = X[column].apply(lambda x: " ".join(x))

        return X

    def transform(self, X):
        X = self._clean_dataframe(X)

        X['raw_lemmatized'] = self.text_to_lemmatized.transform(X['text'].values)
        X['lemmatized'] = self.remove_stop_words_from_lemmatized.transform(
            X['raw_lemmatized'].values
        )
        X['ngramms'] = self.lemmatized_to_ngramms.transform(X['raw_lemmatized'].values)

        for column in ['raw_lemmatized', 'lemmatized', 'ngramms']:
            X[column] = X[column].apply(lambda x: " ".join(x))

        return X

    def _clean_dataframe(self, X):
        X['text'] = X['text'].astype(str).str.strip()
        X = X[X['text'] != '']

        return X

In [ ]:
preprocesser = MainModelPreprocessor(n_jobs=10, verbose=True)
wiki_processed = preprocesser.fit_transform(data_df)

Start of pipeline
**************************************************************************

Start of replacer fit transform
    Start of pipeline
    **********************************************************************

    Start of html_tag_replacer fit transform
    End of html_tag_replacer fit transform
    Total time: 0.14466452598571777
    ------------------------------------------------------------------
    Start of quout_replacer fit transform
    End of quout_replacer fit transform
    Total time: 0.11232948303222656
    ------------------------------------------------------------------
    Start of url_replacer fit transform
    End of url_replacer fit transform
    Total time: 0.9230499267578125
    ------------------------------------------------------------------
    Start of mail_replacer fit transform
    End of mail_replacer fit transform
    Total time: 10.334765911102295
    ------------------------------------------------------------------
    Start of delete_ad

In [14]:
wiki_processed.head()

categories  id  \
0  [Санкт-Петербург, Всемирное наследие в России,...  45   
1  [Карл Росси, Эрмитаж, Художественные музеи и г...  49   
2  [Греко-персидские войны, Войны Древней Греции,...  61   
3                                      [Тихий океан]  98   
4                              [Атлантический океан]  99   

                                                text                   title  \
0  Санкт-Петербург\n\nСанкт-Петербу́рг (с года до...         Санкт-Петербург   
1  Дворцовая площадь\n\nДворцо́вая пло́щадь (с 19...       Дворцовая площадь   
2  Греко-персидские войны\n\nГреко-персидские вой...  Греко-персидские войны   
3  Тихий океан\n\nТи́хий океа́н (устар. "Великий ...             Тихий океан   
4  Атлантический океан\n\nАтланти́ческий океа́н —...     Атлантический океан   

                                      url  \
0  https://ru.wikipedia.org/wiki?curid=45   
1  https://ru.wikipedia.org/wiki?curid=49   
2  https://ru.wikipedia.org/wiki?curid=61   
3  https://ru.wikipedia.org/wiki?curid=98   
4  https://ru.wikipedia.org/wiki?curid=99   

                                      raw_lemmatized  \
0  санкт-петербург санкт-петербург ( с год до 26 ...   
1  дворцовый площадь дворцовый площадь ( с 1918 д...   
2  грёкий - персидский война грёкий - персидский ...   
3  тихий океан тихий океан ( устарый . " великий ...   
4  атлантический океан атлантический океан — два ...   

                                          lemmatized  \
0  год год петроград год год ленинград численност...   
1  дворцовый площадь дворцовый площадь площадь ур...   
2  грёкий персидский война грёкий персидский войн...   
3  тихий океан тихий океан устарый . великий океа...   
4  атлантический океан атлантический океан величи...   

                                             ngramms  
0  санкт_петербург санкт_петербург санкт_петербур...  
1  дворцовый_площадь дворцовый_площадь дворцовый_...  
2  персидский_война персидский_война персидский_в...  
3  тихий_океан тихий_океан тихий_океан тихий_океа...  
4  атлантический_океан атлантический_океан атлант...

In [61]:
wiki_processed.title = wiki_processed.title.str.replace(':', '&#58;').replace('@', '&#64;')




In [66]:
ALL_MODALITIES = ['lemmatized', 'ngramms', 'categories']

def create_vowpal_wabbit(data, modalities=None, use_counters=False):

    sessions_bow_messages = dict()

    for elem_id, elem in data.iterrows():
        if use_counters:
            sessions_bow_messages[elem_id] = {m: Counter() for m in ALL_MODALITIES}
        else:
            sessions_bow_messages[elem_id] = {m: '' for m in ALL_MODALITIES}
        sessions_bow_messages[elem_id]['plain_text'] = ''

        if isinstance(elem.text, str):
            sessions_bow_messages[elem_id]['plain_text'] += ' '.join(elem.text.split()) + ' | '

        for modality in ["lemmatized", "ngramms", "categories"]:
            if isinstance(elem[modality], str):
                tokens = elem[modality].split()
                tokens = [re.sub('[\:\|\@]', '', token) for token in tokens]
            elif isinstance(elem[modality], list):
                tokens = [
                    re.sub('[\:\|\@ ]', '_', token.strip())
                    for token in elem[modality]
                ]

            if use_counters:
                sessions_bow_messages[elem_id][modality] += Counter(tokens)
            else:
                sessions_bow_messages[elem_id][modality] += ' '.join(tokens)

    sessions_bow_messages_str_format = []

    for key in sessions_bow_messages.keys():
        new_message_str_format = str(key).replace(" ", "_")
        if modalities is None:
            modalities = sessions_bow_messages[key].keys()
        for modality in modalities:
            if modality == 'plain_text':
                continue
            if use_counters:
                modality_content = ' '.join([
                    token + ':' + str(count)
                    for token, count in sessions_bow_messages[key][modality].items()
                ])
            else:
                modality_content = sessions_bow_messages[key][modality]
            new_message_str_format += " |@{} {}".format(modality, modality_content)
        sessions_bow_messages_str_format.append(new_message_str_format)
    return sessions_bow_messages_str_format



In [67]:
sessions_bow_messages_str_format = create_vowpal_wabbit(wiki_processed.set_index("title"), use_counters=True)



In [68]:
output = 'good_ruwiki_vw.txt'

with open(output, 'w') as f:
    for elem in sessions_bow_messages_str_format:
        f.write(elem + '\n')

In [65]:
! head good_ruwiki_vw.txt -n 1

Санкт-Петербург |@lemmatized год:301 петроград:7 ленинград:18 численность:14 население:33 город:212 россия:32 .:677 федеральный:15 значение:8 административный:5 центр:29 округа:3 ленинградский:16 область:6 основать:5 царь:3 <person>:195 являться:34 столица:19 российский:35 государство:9 назвать:4 честь:6 святой:11 небесный:2 покровитель:2 основатель:3 время:17 стать:25 большой:23 ассоциироваться:1 имя:34 исторически:1 культурно:1 связать:2 рождение:1 империя:7 вхождение:1 современный:7 история:11 роль:5 европейский:3 великий:5 держава:1 расположить:11 страна:16 побережье:4 финский:16 залив:15 устье:4 река:21 нева:31 находиться:17 конституционный:1 суд:5 федерация:14 геральдический:2 совет:8 президент:1 орган:6 власть:11 межпарламентский:3 ассамблея:3 снг:2 разместить:1 главный:9 командование:2 флот:1 штаб:2 западный:8 военный:8 вооружённый:3 сила:6 быть:74 революция:6 февральский:2 октябрьский:6 ход:4 отечественный:4 война:10 блокада:7 результат:12 миллион:37 человек:39 погибнуть:4 объ

In [ ]:
! ls